In [1]:
import pandas as pd
import numpy as np
import os
import glob
import sys

In [2]:
%load_ext autoreload
%autoreload 2

In [59]:
WIN = 'D:/'
MAC = '/Volumes/Transcend2/17_20_PhD/19_20_PhD_Metabolomics/'

osp = MAC

## Load in limma results

Data was obtained in Step 1/6.PeakSetFiltering

In [11]:
output_dir = osp+'/negative_mode/samples/'
limma_filename = 'limma_independent_toptable_features.csv'


## Run mummichog

In [18]:
keyword = 'mm271020'
os.system('mummichog -f'+ output_dir + limma_filename +
          ' -m negative -u 3 -k MummichogResults -o '+ keyword+' -c 0.05')

0

## Annotate data

In [4]:
keyword = 'mm211020'
for f in os.listdir('MummichogResults'):
    if keyword in f:
        mummichog_folder = f

In [5]:
compounds = pd.read_csv('MummichogResults/'+mummichog_folder+'/tables/ListOfEmpiricalCompounds.tsv', sep='\t')
featureoutput = pd.read_csv('MummichogResults/'+mummichog_folder+'/tables/userInputData.txt', sep='\t')
pathway = pd.read_csv('MummichogResults/'+mummichog_folder+'/tables/mcg_pathwayanalysis_'+keyword+'.tsv', sep='\t')

In [6]:
matching_ids = {}
for _,row in featureoutput.iterrows():
    key = row['massfeature_rows']
    value = row['CompoundID_from_user']
    matching_ids[key] = value

In [7]:
compounds_dict = {}
for _,row in compounds.iterrows():
    ids = row['massfeature_rows']
    ions = row['str_row_ion']
    compoundlist = row['compound_names']
    kegg_id = row['compounds']
    
    
    ids_list = ids.split(';')
    ions_list = ions.split(';')
    for i in range(len(ids_list)):
        compounds_dict[matching_ids[ids_list[i]]] = []
        compounds_dict[matching_ids[ids_list[i]]].append(ions_list[i].split('_')[1])
        compounds_dict[matching_ids[ids_list[i]]].append(compoundlist)
        compounds_dict[matching_ids[ids_list[i]]].append(kegg_id)
        

In [8]:
ecomp_dict = {}
for _,row in compounds.iterrows():
    eid = row['EID']
    massfeature_rows = row['massfeature_rows'].split(';')
    for mass in massfeature_rows:
        if mass in ecomp_dict:
            ecomp_dict[mass].append(eid)
        else:
            ecomp_dict[mass] = []
            ecomp_dict[mass].append(eid)
            
cmpd_names = {}
for _,row in compounds.iterrows():
    eid = row['EID']
    name = row['compound_names']
    cmpd_names[eid] = name
matching_ids = {}
for _,row in featureoutput.iterrows():
    key = row['massfeature_rows']
    value = row['CompoundID_from_user']
    
    matching_ids[value] = key
for n in matching_ids:
    if matching_ids[n] in ecomp_dict:
        matching_ids[n] = ecomp_dict[matching_ids[n]]

id_names = {}
for i in matching_ids:
    if type(matching_ids[i]) is list:
        for f in matching_ids[i]:
            if f in cmpd_names:
                if i in id_names:
                    id_names[i].append(cmpd_names[f])
                else:
                    id_names[i] = []
                    id_names[i].append(cmpd_names[f])
matching_ids2 = {}
for n in matching_ids:
    
    if type(matching_ids[n]) is list:
        lista = matching_ids[n]
        for p in lista:
            if p in matching_ids2:
                matching_ids2[p].append(n)
            else:
                matching_ids2[p] = []
                matching_ids2[p].append(n)
pathway_dict = {}
for _,row in pathway.iterrows():
    
    pname = row['pathway']
    idlist =row['overlap_EmpiricalCompounds (id)']
    
    if type(idlist) != float:
        idlist = idlist.split(',')
        for p in idlist:
            
            if pname in pathway_dict:
                if p in matching_ids2:
                    pathway_dict[pname].append(matching_ids2[p]) 
                
            else:
                pathway_dict[pname] = []
                if p in matching_ids2:
                    pathway_dict[pname].append(matching_ids2[p]) 
                
pathway_dict2 = {}
for p in pathway_dict:
    
    for n in pathway_dict[p]:
        for i in n:
            if i in pathway_dict2:
                if p not in  pathway_dict2[i]:
                    pathway_dict2[i].append(p)
            else:
                pathway_dict2[i] = []
                pathway_dict2[i].append(p)
                

In [24]:
data = pd.read_csv(output_dir+limma_filename, sep='\t')

In [25]:
data.index = data['custom_id']

In [9]:
sys.path.append('..')
import peakinfo
import pickle
sys.path.append('/Users/anamaria/git/molnet/code/')
with open(osp+'positive_mode/samples/peakinfolist.dict', 'rb') as file:
    peakinfolist = pickle.load(file)

In [10]:
for row_id,row in data.iterrows():
    peak = peakinfo.get_peak_by_cid(peakinfolist, row_id)
    if row_id in id_names:
        peak.add_mm_annotation([str(name).lower() for name in id_names[row_id]])
    if row_id in pathway_dict2:
        peak.add_mm_pathway(pathway_dict2[row_id])
    if row_id in compounds_dict:
        peak.add_mm_kegg_id(compounds_dict[row_id][2])   

NameError: name 'data' is not defined

In [28]:
with open(osp+'negative_mode/samples/peakinfolist.dict', 'wb') as handle:
    pickle.dump(peakinfolist, handle)

## Read previous mmumichog results and analyse pathways

In [12]:
def get_peak_by_id(cid):
    cid = 'p'+str(cid)
    for peak in peakinfolist:
        if peak.cid == cid:
            return peak

In [13]:
import os, pickle
with open(os.path.join(osp,'Metabolomics_datasets/metabolites.dict'), 'rb') as file:
    metabolites = pickle.load(file)

In [14]:
for pathway in pathway_dict:
    print(pathway)
    print(pathway_dict[pathway])
    for sets in pathway_dict[pathway]:
        for cid in sets:
            print(cid)
            peak = get_peak_by_id(cid)
            print(peak)
            print(peak.get_possible_kegg_ids())
            print(peak.get_taxonomy(metabolites))
        print('------')

Nitrogen metabolism
[[613, 926, 101, 365, 634, 344], [614, 367], [366], [425], [109, 259, 631], [615], [424], [365, 630, 658, 258, 107]]
613
Peak p613: m/z = 147.07640748274954, rt = 11.905213776127336 

                p-val: 9.50855356149344e-10, logFC = -2.63034608332642 

                mm annotation: ['l-glutamine$3-ureidoisobutyrate$d-glutamine; d-2-aminoglutaramic acid', '5,6-dihydrothymine'] 

                std annotation: l-glutamine 

                hmdb annotation: L-Lysine 

                
                {'frag_pos_mal': <mnet.Spectrum object at 0x11a0a74f0>, 'gnps2': <mnet.Spectrum object at 0x11a0a75b0>} 

['C00906' 'C00064' 'C00047']
[('Dihydrothymine', 'Pyrimidines and pyrimidine derivatives'), ('L-Glutamine', 'Amino acids, peptides, and analogues'), ('L-Lysine', 'Amino acids, peptides, and analogues')]
926
Peak p926: m/z = 169.05836848208781, rt = 11.897038272605002 

                p-val: 1.0322050457876e-08, logFC = -2.1962780494017102 

                mm an

[('Ureidopropionic acid', 'Ureas'), ('L-Asparagine', 'Amino acids, peptides, and analogues'), ('Creatine', 'Amino acids, peptides, and analogues')]
------
365
Peak p365: m/z = 130.04992655703896, rt = 11.890277826892214 

                p-val: 3.36078143804683e-08, logFC = -1.06619681316973 

                mm annotation: ['l-glutamine$3-ureidoisobutyrate$d-glutamine; d-2-aminoglutaramic acid', '5-oxoproline$l-1-pyrroline-3-hydroxy-5-carboxylate$1-pyrroline-4-hydroxy-2-carboxylate', 'd-glutamate; d-glutamic acid; d-glutaminic acid; d-2-aminoglutaric acid$l-glutamate$l-4-hydroxyglutamate semialdehyde', '5-oxo-l-proline'] 

                std annotation:  

                hmdb annotation:  

                
                {'gnps2': <mnet.Spectrum object at 0x1198a8730>} 

['C02238' '']
[]
630
Peak p630: m/z = 148.06041998612253, rt = 11.758435423886752 

                p-val: 0.0631847994645528, logFC = 0.316353248005402 

                mm annotation: ['5-oxoproline$l-1-pyrrolin

[('L-Tryptophan', 'Indolyl carboxylic acids and derivatives'), ('D-Tryptophan', 'Indolyl carboxylic acids and derivatives'), ('L-Tryptophan', 'Indolyl carboxylic acids and derivatives'), ('L-Tryptophan', 'Indolyl carboxylic acids and derivatives')]
1448
Peak p1448: m/z = 206.10056927329612, rt = 9.956545273972079 

                p-val: 0.0220147569905578, logFC = -0.313925099612799 

                mm annotation: ['l-tryptophan$d-tryptophan'] 

                std annotation:  

                hmdb annotation:  

                
                {} 

['C00078' 'C00525' '']
[('L-Tryptophan', 'Indolyl carboxylic acids and derivatives'), ('D-Tryptophan', 'Indolyl carboxylic acids and derivatives')]
------
4109
Peak p4109: m/z = 287.0999953746796, rt = 6.720339472803318 

                p-val: 0.00605037574182198, logFC = -5.28264613797675 

                mm annotation: ['alpha-n-phenylacetyl-l-glutamine$formyl-n-acetyl-5-methoxykynurenamine'] 

                std annotation:  

  

[('D-Glucose', 'Carbohydrates and carbohydrate conjugates'), ('D-Fructose', 'Carbohydrates and carbohydrate conjugates'), ('myo-Inositol', 'Alcohols and polyols'), ('D-Galactose', 'Carbohydrates and carbohydrate conjugates'), ('D-Mannose', 'Carbohydrates and carbohydrate conjugates')]
------
Alanine and Aspartate Metabolism
[[613, 926, 101, 365, 634, 344], [614, 367], [366], [425], [109, 259, 631], [615], [424], [365, 630, 658, 258, 107], [798, 1037, 1053, 1337]]
613
Peak p613: m/z = 147.07640748274954, rt = 11.905213776127336 

                p-val: 9.50855356149344e-10, logFC = -2.63034608332642 

                mm annotation: ['l-glutamine$3-ureidoisobutyrate$d-glutamine; d-2-aminoglutaramic acid', '5,6-dihydrothymine'] 

                std annotation: l-glutamine 

                hmdb annotation: L-Lysine 

                
                {'frag_pos_mal': <mnet.Spectrum object at 0x11a0a74f0>, 'gnps2': <mnet.Spectrum object at 0x11a0a75b0>} 

['C00906' 'C00064' 'C00047']
[('Di

[('L-Glutamine', 'Amino acids, peptides, and analogues'), ('Ureidoisobutyric acid', 'Ureas')]
101
Peak p101: m/z = 101.07095439850336, rt = 11.929978879334824 

                p-val: 1.56737811890671e-08, logFC = -10.0563554026259 

                mm annotation: ['l-glutamine$3-ureidoisobutyrate$d-glutamine; d-2-aminoglutaramic acid', '5,6-dihydrothymine'] 

                std annotation:  

                hmdb annotation:  

                
                {} 

['C00906' '']
[('Dihydrothymine', 'Pyrimidines and pyrimidine derivatives')]
365
Peak p365: m/z = 130.04992655703896, rt = 11.890277826892214 

                p-val: 3.36078143804683e-08, logFC = -1.06619681316973 

                mm annotation: ['l-glutamine$3-ureidoisobutyrate$d-glutamine; d-2-aminoglutaramic acid', '5-oxoproline$l-1-pyrroline-3-hydroxy-5-carboxylate$1-pyrroline-4-hydroxy-2-carboxylate', 'd-glutamate; d-glutamic acid; d-glutaminic acid; d-2-aminoglutaric acid$l-glutamate$l-4-hydroxyglutamate semialdehy

...

[('L-Threonine', 'Amino acids, peptides, and analogues')]
258
Peak p258: m/z = 120.0655581323724, rt = 11.604727263387215 

                p-val: 0.664445243495768, logFC = 0.0597256686249992 

                mm annotation: ['d-glutamate; d-glutamic acid; d-glutaminic acid; d-2-aminoglutaric acid$l-glutamate$l-4-hydroxyglutamate semialdehyde', 'l-allo-threonine$l-threonine'] 

                std annotation: l-homoserine 

                hmdb annotation: L-Threonine 

                
                {'frag_pos_vl': <mnet.Spectrum object at 0x1196e5430>} 

['C05519' 'C00188' 'C00263' 'C00188']
[('L-Threonine', 'Amino acids, peptides, and analogues'), ('L-Homoserine', 'Amino acids, peptides, and analogues'), ('L-Threonine', 'Amino acids, peptides, and analogues')]
107
Peak p107: m/z = 102.05497400084538, rt = 11.59886927335523 

                p-val: 0.8438870201350841, logFC = -0.312855419792593 

                mm annotation: ['5-oxoproline$l-1-pyrroline-3-hydroxy-5-carboxylate$1

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




------
366
Peak p366: m/z = 130.04995717500387, rt = 9.235738236152981 

                p-val: 1.69222685515447e-05, logFC = -0.649141706140043 

                mm annotation: ['5-oxoproline$l-1-pyrroline-3-hydroxy-5-carboxylate$1-pyrroline-4-hydroxy-2-carboxylate$5-oxo-l-proline', 'd-glutamate; d-glutamic acid; d-glutaminic acid; d-2-aminoglutaric acid$l-glutamate$l-4-hydroxyglutamate semialdehyde'] 

                std annotation: 5-oxoproline 

                hmdb annotation: Pipecolic acid 

                
                {'frag_pos_mal': <mnet.Spectrum object at 0x1198fa370>, 'frag_pos_vl': <mnet.Spectrum object at 0x1198fa430>} 

['C00217' 'C00025' 'C05938' '' 'C00408']
[('D-Glutamic acid', 'Amino acids, peptides, and analogues'), ('L-Glutamic acid', 'Amino acids, peptides, and analogues'), ('Pipecolic acid', 'Amino acids, peptides, and analogues'), ('L-Pipecolic acid', 'Amino acids, peptides, and analogues')]
------
Butanoate metabolism
[[109, 259, 631], [365, 630, 658, 2

['C00217' 'C00025' 'C05938' '' 'C00408']
[('D-Glutamic acid', 'Amino acids, peptides, and analogues'), ('L-Glutamic acid', 'Amino acids, peptides, and analogues'), ('Pipecolic acid', 'Amino acids, peptides, and analogues'), ('L-Pipecolic acid', 'Amino acids, peptides, and analogues')]
------
599
Peak p599: m/z = 146.08119874251517, rt = 8.329311348282669 

                p-val: 0.0060061446619100395, logFC = 0.516617388800999 

                mm annotation: ['6-amino-2-oxohexanoate; 2-oxo-6-aminocaproate$4-acetamidobutanoate$l-2-aminoadipate 6-semialdehyde; 2-aminoadipate 6-semialdehyde'] 

                std annotation:  

                hmdb annotation:  

                
                {'frag_pos_mal': <mnet.Spectrum object at 0x119e60790>, 'frag_pos_vl': <mnet.Spectrum object at 0x119e60850>} 

['C03239' 'C02946' 'C04076' '']
[('4-Acetamidobutanoic acid', 'Amino acids, peptides, and analogues')]
------
Urea cycle/amino group metabolism
[[366], [599], [667, 690, 121, 423, 678]

['C05519' 'C00188' '']
[('L-Threonine', 'Amino acids, peptides, and analogues')]
631
Peak p631: m/z = 148.06044561212713, rt = 9.599390270895464 

                p-val: 0.788679225023558, logFC = 0.34580376533525803 

                mm annotation: ['d-glutamate; d-glutamic acid; d-glutaminic acid; d-2-aminoglutaric acid$l-glutamate$l-4-hydroxyglutamate semialdehyde', 'dl-glutamate; dl-glutaminic acid; 2-aminoglutaric acid; glutamate'] 

                std annotation:  

                hmdb annotation:  

                
                {} 

['C00302' '']
[]
------
365
Peak p365: m/z = 130.04992655703896, rt = 11.890277826892214 

                p-val: 3.36078143804683e-08, logFC = -1.06619681316973 

                mm annotation: ['l-glutamine$3-ureidoisobutyrate$d-glutamine; d-2-aminoglutaramic acid', '5-oxoproline$l-1-pyrroline-3-hydroxy-5-carboxylate$1-pyrroline-4-hydroxy-2-carboxylate', 'd-glutamate; d-glutamic acid; d-glutaminic acid; d-2-aminoglutaric acid$l-glutamate$l-4-

In [25]:
metabolites

{'HMDB0000001': ('169.1811',
  'C7H11N3O2',
  '1-Methylhistidine',
  'CN1C=NC(C[C@H](N)C(O)=O)=C1',
  '3741',
  'C01152',
  None,
  'Carboxylic acids and derivatives',
  'Amino acids, peptides, and analogues',
  'Aromatic heteromonocyclic compounds'),
 'HMDB0000002': ('74.1249',
  'C3H10N2',
  '1,3-Diaminopropane',
  'NCCCN',
  '5081',
  'C00986',
  None,
  'Organonitrogen compounds',
  'Amines',
  'Aliphatic acyclic compounds'),
 'HMDB0000005': ('102.0886',
  'C4H6O3',
  '2-Ketobutyric acid',
  'CCC(=O)C(O)=O',
  None,
  'C00109',
  None,
  'Keto acids and derivatives',
  'Short-chain keto acids and derivatives',
  'Aliphatic acyclic compounds'),
 'HMDB0000008': ('104.1045',
  'C4H8O3',
  '2-Hydroxybutyric acid',
  'CCC(O)C(O)=O',
  '3783',
  'C05984',
  'map00640',
  'Hydroxy acids and derivatives',
  'Alpha hydroxy acids and derivatives',
  'Aliphatic acyclic compounds'),
 'HMDB0000010': ('300.3921',
  'C19H24O3',
  '2-Methoxyestrone',
  '[H][C@@]12CCC(=O)[C@@]1(C)CC[C@]1([H])C3=C(C

In [43]:
taxdict = {}
for peak in peakinfolist:
    if peak.pval <0.05 and peak.pval != 0 and peak.cid not in ['p459', 'p690', 'p2384']:
        #print(peak)
        #print(peak.get_possible_kegg_ids())
        taxonomy = peak.get_taxonomy(metabolites)
        
        if peak.std_annotation != '':
            std = 'std'
        else:
            std = ''
            
        if taxonomy != None:
    
            taxdict[peak.cid] = (std, peak.std_annotation, taxonomy)
            
        #print(std, peak.std_annotation, taxonomy)

In [44]:
taxdict

{'p38': ('',
  '',
  [('L-Threonine', 'Amino acids, peptides, and analogues'),
   ('Pipecolic acid', 'Amino acids, peptides, and analogues'),
   ('L-Pipecolic acid', 'Amino acids, peptides, and analogues')]),
 'p101': ('',
  '',
  [('Dihydrothymine', 'Pyrimidines and pyrimidine derivatives')]),
 'p109': ('', '', [('L-Threonine', 'Amino acids, peptides, and analogues')]),
 'p121': ('', '', [('L-Methionine', 'Amino acids, peptides, and analogues')]),
 'p122': ('',
  '',
  [('L-alpha-Aminobutyric acid', 'Amino acids, peptides, and analogues'),
   ('Dimethylglycine', 'Amino acids, peptides, and analogues'),
   ('gamma-Aminobutyric acid', 'Amino acids, peptides, and analogues'),
   ('3-Aminoisobutanoic acid', 'Amino acids, peptides, and analogues'),
   ('(S)-b-aminoisobutyric acid', 'Amino acids, peptides, and analogues'),
   ('Dimethylglycine', 'Amino acids, peptides, and analogues')]),
 'p134': ('',
  '',
  [('L-alpha-Aminobutyric acid', 'Amino acids, peptides, and analogues'),
   ('Dimet

In [29]:
print(get_peak_by_id(459).get_possible_kegg_ids())

['C00155' None]


In [24]:
metabolites

{'HMDB0000001': ('169.1811',
  'C7H11N3O2',
  '1-Methylhistidine',
  'CN1C=NC(C[C@H](N)C(O)=O)=C1',
  '3741',
  'C01152',
  None,
  'Carboxylic acids and derivatives',
  'Amino acids, peptides, and analogues',
  'Aromatic heteromonocyclic compounds'),
 'HMDB0000002': ('74.1249',
  'C3H10N2',
  '1,3-Diaminopropane',
  'NCCCN',
  '5081',
  'C00986',
  None,
  'Organonitrogen compounds',
  'Amines',
  'Aliphatic acyclic compounds'),
 'HMDB0000005': ('102.0886',
  'C4H6O3',
  '2-Ketobutyric acid',
  'CCC(=O)C(O)=O',
  None,
  'C00109',
  None,
  'Keto acids and derivatives',
  'Short-chain keto acids and derivatives',
  'Aliphatic acyclic compounds'),
 'HMDB0000008': ('104.1045',
  'C4H8O3',
  '2-Hydroxybutyric acid',
  'CCC(O)C(O)=O',
  '3783',
  'C05984',
  'map00640',
  'Hydroxy acids and derivatives',
  'Alpha hydroxy acids and derivatives',
  'Aliphatic acyclic compounds'),
 'HMDB0000010': ('300.3921',
  'C19H24O3',
  '2-Methoxyestrone',
  '[H][C@@]12CCC(=O)[C@@]1(C)CC[C@]1([H])C3=C(C

In [49]:
df = pd.DataFrame(taxdict).transpose()

In [56]:
df.to_csv('/Users/anamaria/Desktop/metab.csv')

In [58]:
pd.DataFrame(df[2].to_list(), index = df.index)

0  \
p38    (L-Threonine, Amino acids, peptides, and analo...   
p101   (Dihydrothymine, Pyrimidines and pyrimidine de...   
p109   (L-Threonine, Amino acids, peptides, and analo...   
p121   (L-Methionine, Amino acids, peptides, and anal...   
p122   (L-alpha-Aminobutyric acid, Amino acids, pepti...   
...                                                  ...   
p4370                                               None   
p4735                                               None   
p4907                                               None   
p6582                                               None   
p6915                                               None   

                                                       1  \
p38    (Pipecolic acid, Amino acids, peptides, and an...   
p101                                                None   
p109                                                None   
p121                                                None   
p122   (Dimethylglycine, Amino acids, peptides, and a...   
...                                                  ...   
p4370                                               None   
p4735                                               None   
p4907                                               None   
p6582                                               None   
p6915                                               None   

                                                       2  \
p38    (L-Pipecolic acid, Amino acids, peptides, and ...   
p101                                                None   
p109                                                None   
p121                                                None   
p122   (gamma-Aminobutyric acid, Amino acids, peptide...   
...                                                  ...   
p4370                                               None   
p4735                                               None   
p4907                                               None   
p6582                                               None   
p6915                                               None   

                                                       3  \
p38                                                 None   
p101                                                None   
p109                                                None   
p121                                                None   
p122   (3-Aminoisobutanoic acid, Amino acids, peptide...   
...                                                  ...   
p4370                                               None   
p4735                                               None   
p4907                                               None   
p6582                                               None   
p6915                                               None   

                                                       4  \
p38                                                 None   
p101                                                None   
p109                                                None   
p121                                                None   
p122   ((S)-b-aminoisobutyric acid, Amino acids, pept...   
...                                                  ...   
p4370                                               None   
p4735                                               None   
p4907                                               None   
p6582                                               None   
p6915                                               None   

                                                       5  
p38                                                 None  
p101                                                None  
p109                                                None  
p121                                                None  
p122   (Dimethylglycine, Amino acids, peptides, and a...  
...                                                  ...  
p4370                                

## Matching with standards ToxID annotation

In [29]:
import pickle
with open(osp+'Metabolomics_datasets/standards_list.dict', 'rb') as file:
    standards_dict = pickle.load(file)

In [32]:
import metab_utils
standards_list_file = "/Volumes/Transcend2/17_20_PhD/19_20_PhD_Metabolomics/Metabolomics_datasets/standards_list.csv"
standards = pd.read_csv(standards_list_file)
standards_list = metab_utils.create_std_dict_by_mz(standards, polarity = '-')
with open(osp+'negative_mode/standards_list.dict', 'wb') as handle:
    pickle.dump(standards_list, handle)

In [34]:
standards_list

{353.04926: ('phenolsulfonphthalein', 341.40000000000003, '-', 237563187),
 241.08319: ('thymidine', 387.0, '-', 55965922),
 208.06512: ('mops', 421.8, '-', 93178795),
 87.00878: ('pyruvate', 490.2, '-', 9196824),
 227.0676: ('deoxyuridine', 459.0, '-', 38943631),
 163.04023999999998: ('4-coumarate', 478.8, '-', 137879575),
 123.02008000000001: ('pyrazinoate', 513.0, '-', 12085996),
 103.04008: ('(r)-3-hydroxybutanoate', 530.4, '-', 27365508),
 328.04562000000004: ("3'_5'-cyclic amp", 528.0, '-', 41469443),
 243.06239: ('uridine', 549.6, '-', 54886480),
 179.05638000000002: ('d-glucose', 755.4, '-', 808433),
 155.00993: ('orotate', 583.8000000000001, '-', 237865845),
 163.06145: ('l-rhamnose', 609.6, '-', 429088),
 151.02632: ('xanthine', 630.0, '-', 3045272),
 167.03513999999998: ('3_4-dihydroxyphenylacetate', 709.2, '-', 3054178),
 165.01945: ('phthalate', 721.1999999999999, '-', 703934845),
 195.05125: ('d-gluconic acid', 714.0, '-', 47479612),
 323.02896: ('ump', 696.5999999999999,

In [17]:
peakset = {}
for _, row in data.iterrows():
    cid = row['custom_id']
    mz = row['row m/z']
    rt = row['row retention time']
    pval = row['adj-p']
    tval = row['t-val']
    mm_name = row['mm_compound_names']
    mm_path = row['mm_pathway']
    mm_kegg = row['mm_kegg_id']
    std = row['std_match']
    
    peakset[cid] = (mz, rt*60, pval, tval, mm_name, mm_path, mm_kegg, std)

In [18]:
with open(osp+'pymz/mzmine/peak_picked_files/filtered_peaksets.dict', 'wb') as handle:
    pickle.dump(peakset, handle)

## Check accuracy of mummichog annotation

In [17]:
notannotated = 0
annotated = 0
notannotateds = 0
annotateds = 0
match = 0
matchs =0
for i,row in data.iterrows():
    cmp = str(row['mm_compound_names']).lower()
    std = str(row['std_match']).lower()
    
    if cmp in ['nan']:
        notannotated +=1
        if not std in ['nan']:
            matchs +=1
           
    else:
        annotated +=1
        if not std in ['nan']:
            if std in cmp:
                match +=1
            else:
                print(row)
    
    if std in ['nan']:
        notannotateds +=1
    else:
        annotateds +=1
        
percentage_exact_matches = match*100/annotateds
percentage_not_annotated = matchs*100/annotateds
percentage_not_matched = (annotateds-match-matchs)*100/annotateds

print("Total number of annotated compounds using mummichog: {}".format(annotated))
print("Total number of annotated compounds using ToxID standards: {}".format(annotateds))
print("Total number of annotation matches between mummichog and ToxID: {0}, i.e. {1:.2f}%".format(match, percentage_exact_matches))
print("Total number of annotation mismatches between mummichog and ToxID: {0}, i.e. {1:.2f}%".format(annotateds-match-matchs, percentage_not_matched))
print("Total number of metabolites annotated with ToxID, but not with mummichog: {0}, i.e. {1:.2f}%".format(matchs, percentage_not_annotated))

KeyError: 'mm_compound_names'

In [60]:
df = pd.read_csv(osp+'pymz/mzmine/peak_picked_files/limma_independent_toptable.csv')

In [61]:
df

logFC    AveExpr         t       P.Value     adj.P.Val          B
3022  -11.331295  18.021029 -8.690375  5.255238e-13  2.670170e-10  19.288218
1517  -10.248729  15.637065 -8.572486  8.841622e-13  2.670170e-10  18.778514
2947   -2.089988  22.334270 -8.222488  4.142949e-12  8.341137e-10  17.265520
1401    2.549193  24.597785  7.889092  1.800742e-11  2.719120e-09  15.826641
101    -2.088202  22.460491 -7.767609  3.073015e-11  3.712202e-09  15.303442
...          ...        ...       ...           ...           ...        ...
10779  -0.006983  27.613929 -0.032195  9.744013e-01  9.808212e-01  -6.871329
2057    0.007572  22.662110  0.030247  9.759495e-01  9.808212e-01  -6.871390
2476    0.004093  21.103003  0.015505  9.876699e-01  9.909512e-01  -6.871728
1393   -0.001946  20.756899 -0.012650  9.899398e-01  9.915815e-01  -6.871769
743    -0.000101  21.202736 -0.000539  9.995716e-01  9.995716e-01  -6.871849

[604 rows x 6 columns]